In [1]:
import pandas as pd
import numpy as np
import os, sys, gc
from tqdm.notebook import tqdm

In [2]:
path = './t-academy-data/'

In [3]:
books = pd.read_csv(path + "books.csv")
book_tags = pd.read_csv(path + "book_tags.csv")

train = pd.read_csv(path + "train.csv")
test = pd.read_csv(path + "test.csv")

tags = pd.read_csv(path + "tags.csv")
to_read = pd.read_csv(path + "to_read.csv")

In [4]:
train.shape, test.shape

((477592, 2), (593032, 2))

In [5]:
train.head()

user_id  book_id
0        1     6285
1        2     8034
2        3     9014
3        4     3469
4        5     8072

In [6]:
train['book_id'].nunique()

10000

In [7]:
train['book_id'] = train['book_id'].astype(str)
test['book_id'] = test['book_id'].astype(str)
books['book_id'] = books['book_id'].astype(str)

In [8]:
sol = test.groupby(['user_id'])['book_id'].agg({'unique'}).reset_index()
sol

user_id                                             unique
0            1                                       [1180, 4893]
1            2                                       [9762, 8855]
2            3                                             [9049]
3            4                                       [8464, 3273]
4            5                                 [7487, 6646, 6703]
...        ...                                                ...
53419    53420                           [4625, 5651, 9149, 4086]
53420    53421                     [8513, 8194, 7278, 9334, 9498]
53421    53422  [4613, 6887, 7817, 5811, 1780, 4213, 7667, 875...
53422    53423                                             [8712]
53423    53424  [8609, 4483, 8262, 9255, 8969, 7503, 5301, 421...

[53424 rows x 2 columns]

In [9]:
gt = {}
for user, book_ids in sol.values:
    gt[user] = book_ids.tolist()
gt

{1: ['1180', '4893'],
 2: ['9762', '8855'],
 3: ['9049'],
 4: ['8464', '3273'],
 5: ['7487', '6646', '6703'],
 6: ['7341'],
 7: ['4608',
  '2564',
  '4101',
  '7814',
  '6152',
  '1801',
  '910',
  '2325',
  '4885',
  '7325',
  '2084',
  '2470',
  '3884',
  '6444',
  '6701',
  '1199',
  '1071',
  '2102',
  '3137',
  '1991',
  '585',
  '1484',
  '2766',
  '4944',
  '7377',
  '1620',
  '5332',
  '3672',
  '7128',
  '7003',
  '5341',
  '2782',
  '4190',
  '7904',
  '8413',
  '4964',
  '4459',
  '4588',
  '3711',
  '8432',
  '3314',
  '2045',
  '1918',
  '7807'],
 8: ['9114', '9991'],
 9: ['8676', '4788', '5908', '6777', '7868'],
 10: ['9600',
  '7486',
  '5926',
  '3946',
  '8653',
  '4531',
  '5907',
  '6131',
  '9240',
  '9854'],
 11: ['7269', '9483', '7277', '8175', '8950'],
 12: ['7287'],
 13: ['6723'],
 14: ['4826', '8323', '7604', '5495'],
 15: ['8842'],
 16: ['9858', '6772', '9460'],
 17: ['7063'],
 18: ['8329', '8585', '4054'],
 19: ['7649',
  '4711',
  '7783',
  '4202',
  '6315',

In [10]:
rec_df = pd.DataFrame()
rec_df['user_id'] = train['user_id'].unique()
rec_df

user_id
0            1
1            2
2            3
3            4
4            5
...        ...
53377    53420
53378    53421
53379    53422
53380    53423
53381    53424

[53382 rows x 1 columns]

# Baseline
- 통계기반의 모델

In [11]:
books.sort_values(by='books_count', ascending=False)[:5]

id  book_id  best_book_id   work_id  books_count       isbn  \
9       10     1885          1885   3060926         3455  679783261   
1724  1725  6324090       6324090  55548884         3296        NaN   
70      71    18490         18490   4836639         2618  141439475   
292    293      295           295   3077988         2573  753453800   
42      43    10210         10210   2977639         2568  142437204   

            isbn13                                            authors  \
9     9.780680e+12                                        Jane Austen   
1724           NaN                        Lewis Carroll, John Tenniel   
70    9.780141e+12  Mary Wollstonecraft Shelley, Percy Bysshe Shel...   
292   9.780753e+12                             Robert Louis Stevenson   
42    9.780142e+12                    Charlotte Brontë, Michael Mason   

      original_publication_year                           original_title  ...  \
9                        1813.0                      Pride and Prejudice  ...   
1724                     1865.0                                      NaN  ...   
70                       1818.0  Frankenstein; or, The Modern Prometheus  ...   
292                      1882.0                          Treasure Island  ...   
42                       1847.0                                Jane Eyre  ...   

     ratings_count work_ratings_count  work_text_reviews_count  ratings_1  \
9          2035490            2191465                    49152      54700   
1724         30426              85031                     5047       1724   
70          808589             883563                    19993      29366   
292         268012             310515                     7917       5349   
42         1198557            1286135                    31212      35132   

      ratings_2  ratings_3  ratings_4  ratings_5  \
9         86485     284852     609755    1155673   
1724       4863      18094      27848      32502   
70        74142     231022     300495     248538   
292       19127      86487     114968      84584   
42        64274     212294     400214     574221   

                                              image_url  \
9     https://images.gr-assets.com/books/1320399351m...   
1724  https://images.gr-assets.com/books/1391204048m...   
70    https://images.gr-assets.com/books/1381512375m...   
292   https://images.gr-assets.com/books/1485248909m...   
42    https://images.gr-assets.com/books/1327867269m...   

                                        small_image_url  
9     https://images.gr-assets.com/books/1320399351s...  
1724  https://images.gr-assets.com/books/1391204048s...  
70    https://images.gr-assets.com/books/1381512375s...  
292   https://images.gr-assets.com/books/1485248909s...  
42    https://images.gr-assets.com/books/1327867269s...  

[5 rows x 23 columns]

In [14]:
popular_rec_model = books.sort_values(by='books_count', ascending=False)['book_id'].values[0:500]

In [21]:
total_rec_list = {}
for user in rec_df['user_id'].unique():
    total_rec_list[user] = popular_rec_model[0:200].tolist()

In [22]:
total_rec_list[1] == total_rec_list[100]

True

In [23]:
import six
import math

# https://github.com/kakao-arena/brunch-article-recommendation/blob/master/evaluate.py

class evaluate():
    def __init__(self, recs, gt, topn=100):
        self.recs = recs
        self.gt = gt 
        self.topn = topn 
        
    def _ndcg(self):
        Q, S = 0.0, 0.0
        for u, seen in six.iteritems(self.gt):
            seen = list(set(seen))
            rec = self.recs.get(u, [])
            if not rec or len(seen) == 0:
                continue

            dcg = 0.0
            idcg = sum([1.0 / math.log(i + 2, 2) for i in range(min(len(seen), len(rec)))])
            for i, r in enumerate(rec):
                if r not in seen:
                    continue
                rank = i + 1
                dcg += 1.0 / math.log(rank + 1, 2)
            ndcg = dcg / idcg
            S += ndcg
            Q += 1
        return S / Q


    def _map(self):
        n, ap = 0.0, 0.0
        for u, seen in six.iteritems(self.gt):
            seen = list(set(seen))
            rec = self.recs.get(u, [])
            if not rec or len(seen) == 0:
                continue

            _ap, correct = 0.0, 0.0
            for i, r in enumerate(rec):
                if r in seen:
                    correct += 1
                    _ap += (correct / (i + 1.0))
            _ap /= min(len(seen), len(rec))
            ap += _ap
            n += 1.0
        return ap / n


    def _entropy_diversity(self):
        sz = float(len(self.recs)) * self.topn
        freq = {}
        for u, rec in six.iteritems(self.recs):
            for r in rec:
                freq[r] = freq.get(r, 0) + 1
        ent = -sum([v / sz * math.log(v / sz) for v in six.itervalues(freq)])
        return ent
    
    def _evaluate(self):
        print('MAP@%s: %s' % (self.topn, self._map()))
        print('NDCG@%s: %s' % (self.topn, self._ndcg()))
        print('EntDiv@%s: %s' % (self.topn, self._entropy_diversity()))

In [24]:
evaluate_func = evaluate(recs=total_rec_list, gt = gt, topn=200)
evaluate_func._evaluate()

MAP@200: 0.00015823893987182772
NDCG@200: 0.0018158685751382372
EntDiv@200: 5.298317366548021


# Baseline 응용¶
- 많이 글은 글중에서도 평점이 높은 글들을 우선적으로 추천
- 내가 좋아하는 작가의 글을 우선적으로 추천
- 장바구니에 담긴 글과 작가의 글을 우선적으로 추천
- 읽은 글의 시리즈글이 나오면 추천 (해리포터 마법사의 돌 -> 비밀의 방)
- 최신의 글을 추천

In [26]:
train = pd.merge(train, books[['book_id', 'authors', 'ratings_count']], how='left', on='book_id')
train

user_id book_id                        authors  ratings_count
0             1    6285                            NaN            NaN
1             2    8034                            NaN            NaN
2             3    9014  Richard Bachman, Stephen King        71775.0
3             4    3469                            NaN            NaN
4             5    8072                            NaN            NaN
...         ...     ...                            ...            ...
477587    53424    9849                            NaN            NaN
477588    53424    7212                            NaN            NaN
477589    53424    7833                            NaN            NaN
477590    53424    3602                            NaN            NaN
477591    53424    6455                            NaN            NaN

[477592 rows x 4 columns]

In [27]:
train.isna().sum()

user_id               0
book_id               0
authors          438720
ratings_count    438720
dtype: int64

In [28]:
agg = train.groupby(['user_id', 'authors'])['authors'].agg({'count'}).reset_index()
agg = agg.sort_values(by='count', ascending=False)
agg.head()

user_id      authors  count
20625    33697  Bill Bryson      7
11449    18313  Bill Bryson      7
10970    17566  Bill Bryson      7
10558    16913  Bill Bryson      6
24707    41074  Bill Bryson      6

In [29]:
author_books = books[['book_id', 'authors', 'ratings_count']].sort_values(by=['authors', 'ratings_count'], ascending=[True, False])
author_books = author_books.reset_index(drop=True)

author_books.head()

book_id                        authors  ratings_count
0    101911               A. Manette Ansay          23966
1  16081754            A. Meredith Walters          24615
2  16102880            A. Meredith Walters          24287
3     99107  A.A. Milne, Ernest H. Shepard         207550
4    776407  A.A. Milne, Ernest H. Shepard          69102

In [31]:
author_rec_model = agg.merge(author_books, how='left', on=['authors'])
author_rec_model.head()

user_id      authors  count  book_id  ratings_count
0    33697  Bill Bryson      7     9791         250192
1    33697  Bill Bryson      7       21         191535
2    33697  Bill Bryson      7       28          66947
3    33697  Bill Bryson      7       24          58688
4    33697  Bill Bryson      7  7507825          55296

In [32]:
author_rec_model[author_rec_model['user_id'] == 33697]['book_id'].values

array(['9791', '21', '28', '24', '7507825', '25', '10538', '27', '26',
       '17262366', '135611', '29', '25489012', '10541', '1554', '7728',
       '2880', '2879', '271264', '5205', '5', '3', '15881', '6', '136251',
       '2', '1', '99298', '8', '50', '141372', '2915', '234225', '106',
       '112', '53764', '42432', '117', '105', '8852', '12996', '12938',
       '47021', '12985', '1625', '42607', '569564', '72978', '82356',
       '44133'], dtype=object)

In [35]:
total_rec_list = {}
for user in rec_df['user_id'].unique():
    rec_list = author_rec_model[author_rec_model['user_id'] == user]['book_id'].values.tolist()
    if len(rec_list) < 200:
        rec_list.extend(popular_rec_model[:200-len(rec_list)])
    total_rec_list[user] = rec_list[:200]
total_rec_list

{1: ['1885',
  '6324090',
  '18490',
  '295',
  '10210',
  '6185',
  '24583',
  '5326',
  '5297',
  '2956',
  '17245',
  '51496',
  '14935',
  '18135',
  '1420',
  '54479',
  '3836',
  '10534',
  '153747',
  '18254',
  '7733',
  '8852',
  '1371',
  '2623',
  '8921',
  '7144',
  '6969',
  '157993',
  '1934',
  '1381',
  '33507',
  '2175',
  '28862',
  '6656',
  '12296',
  '15823480',
  '236093',
  '2156',
  '1923820',
  '34268',
  '1852',
  '1622',
  '4900',
  '32829',
  '4671',
  '2998',
  '7190',
  '24280',
  '485894',
  '8127',
  '7126',
  '77270',
  '57854',
  '2493',
  '58696',
  '3590',
  '45032',
  '30597',
  '8909',
  '5659',
  '13006',
  '12938',
  '102868',
  '11012',
  '280111',
  '24128',
  '43035',
  '46787',
  '4934',
  '38296',
  '12996',
  '19380',
  '3685',
  '180617',
  '656',
  '22463',
  '5470',
  '30474',
  '52036',
  '51893',
  '5907',
  '12985',
  '406373',
  '21348',
  '17184',
  '62446',
  '83346',
  '32261',
  '17690',
  '7613',
  '6440',
  '16343',
  '1625',
 

In [51]:
total_rec_list[1] == total_rec_list[3]

False

In [52]:
evaluate_func = evaluate(recs=total_rec_list, gt=gt, topn=200)
evaluate_func._evaluate()

MAP@200: 0.00017293794700473045
NDCG@200: 0.0019651464464105015
EntDiv@200: 5.433168880218885


In [53]:
# 내가 읽은 책의 목록을 추출 
read_list = train.groupby(['user_id'])['book_id'].agg({'unique'}).reset_index()
read_list.head()

user_id        unique
0        1        [6285]
1        2        [8034]
2        3        [9014]
3        4        [3469]
4        5  [8072, 4829]

In [61]:
list(set([5,6,1,2,3,4]).difference(set([3,4])))

[1, 2, 5, 6]

In [62]:
total_rec_list = {}
for user in tqdm(rec_df['user_id'].unique()):
    rec_list = []
    author_rec_model_ = author_rec_model[author_rec_model['user_id'] == user]['book_id'].values
    seen = read_list[read_list['user_id'] == user]['unique'].values[0]
    for rec in author_rec_model_: 
        if rec not in seen:
            rec_list.append(rec)
    
    if len(rec_list) < 200:
        for i in popular_rec_model[0:200]:
            if rec not in seen:
                rec_list.append(rec)

    total_rec_list[user] = rec_list[0:200]

  0%|          | 0/53382 [00:00<?, ?it/s]

In [63]:
evaluate_func = evaluate(recs=total_rec_list, gt = gt, topn=200)
evaluate_func._evaluate()

MAP@200: 0.025911884608231822
NDCG@200: 0.007786018300376279
EntDiv@200: 5.085729810099837
